<a href="https://colab.research.google.com/github/abhilashhn1993/Sentiment_Analysis_of_Tweets/blob/master/TFIDF_and_Classifier.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [68]:
import nltk; 
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [69]:
!pip install spacy

In [0]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
import spacy
import pyLDAvis
import pyLDAvis.gensim
import matplotlib.pyplot as plt
%matplotlib inline
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)

In [0]:
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

In [72]:
print(stop_words)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', '

In [0]:
#remove been, being, haven't, don't, couldn't, didn't
stop_words.remove("i")
stop_words.remove("me")
stop_words.remove("my")
stop_words.remove("don't")
stop_words.remove("been")
stop_words.remove("being")
stop_words.remove("haven't")
stop_words.remove("couldn't")
stop_words.remove("didn't")

In [0]:
#Adding Extra Stopwords to be removed from the dataset
stop_words.extend(['http', 'https', 'twitter', 'www', 'instagram', 'zsgdbw', 'tmblr', 'co', 'twitch','facebook', 'snapchat'])

In [75]:
len(stop_words)

181

In [0]:
stop_words.extend(['make','really','see','go','would','even','get','com','be','year','still','do','know','actually','much', 'let','s','have','name','photo'])

In [0]:
stop_words.extend(['back','today','day','last','thing','kit','stream','amp'])

In [0]:
stop_words.extend(['trinawolfy','trinawolfy','riyenrootsmusic','straw'])

In [79]:
len(stop_words)

213

In [80]:
print(stop_words)

['myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', 'too', 'very', 's', 't', 'can', 'wi

In [15]:
from google.colab import files
uploaded = files.upload()

Saving All_PTSD_tweets_Flagged.csv to All_PTSD_tweets_Flagged.csv


In [0]:
import io
df = pd.read_csv(io.BytesIO(uploaded['All_PTSD_tweets_Flagged.csv']))

In [132]:
df.Ptsd.value_counts()

1    113901
0     72629
Name: Ptsd, dtype: int64

In [0]:
df_bkp = df

In [158]:
df_bkp

Username  ... Ptsd
0       CropxDust  ...    1
1       CropxDust  ...    1
2       CropxDust  ...    1
3       CropxDust  ...    1
4       CropxDust  ...    1
...           ...  ...  ...
186525      xtina  ...    0
186526      xtina  ...    0
186527      xtina  ...    0
186528      xtina  ...    0
186529      xtina  ...    0

[186530 rows x 8 columns]

In [0]:
#Concatenate by username
df = df[['Username', 'Tweets','Ptsd']]
#df1 = df.groupby(['Username','Ptsd'])['Tweets'].apply(list).reset_index(name='Tweets')
df1 = df.groupby(['Username','Ptsd'])['Tweets'].agg(' '.join).reset_index(name='Tweets')

In [184]:
df1.iloc[0].Tweets

'Sucks ass!!! Back at you sweet lady! You too! @KarenUnrue need video lift! Please give if you can. So glad you did that! Hugs You got this Duck! Thank you Donna. I think you are just the best!!  Yes indeed! Awesome We have far too many balls to juggle - folks dementia slide - making new safe home - feel unsafe/unfamiliar - friendship losses - butt pain - hip months pain - high living costs - lack full med coverage - building remodelling daily noise - flashbacks I will race you! Distraction has helped me. Grounding in Now. Breathe lots. I can relate. Tangled branches Buried deep Encased in ice Cold and still Frozen roots To life In dormancy ~A.R.* The is only one you With flaws and all As meant to be Unique and true To self Be your best Fragments of self http://idisassociate.blogspot.com/2016/08/fragments-of-self.html Grounding in the Now http://idisassociate.blogspot.com/2016/12/grounding-in-now.html Help Hotlines http://idisassociate.blogspot.com/2017/07/help-hotlines_5.html The \'No

In [0]:
df1_bkp =df1

In [183]:
df1

Username  Ptsd                                             Tweets
0           AFR365     1  Sucks ass!!! Back at you sweet lady! You too! ...
1     AlishaaHasan     0  0 Omggggg I agreee! Like first of all what eve...
2       AmyRollitt     1  If only f i had come in on my usual day! Such ...
3      BenBarbossa     1  Maybe, maybe not...  The lovely wife calls me ...
4    BethLynch2020     1  same Oh for sure, it's definitely much better ...
..             ...   ...                                                ...
107  sweetderacine     1  i remember being super scared to talk to you b...
108  twilightfairy     0  Great news! Congrats! I remember this discussi...
109      upsetvet1     1  Jail time  0 0 He owns 3 houses, he needs to p...
110      vkhillier     1  lost ur lil ass that u had, playin wit ya nose...
111          xtina     0  Haha omg how sweet is she! Cute!!! Yes!! #Figh...

[112 rows x 3 columns]

In [127]:
type(df1)

pandas.core.frame.DataFrame

In [0]:
# Convert to list
df1.Tweets = df1.Tweets.values.tolist()

In [188]:
df1

Username  Ptsd                                             Tweets
0           AFR365     1  Sucks ass!!! Back at you sweet lady! You too! ...
1     AlishaaHasan     0  0 Omggggg I agreee! Like first of all what eve...
2       AmyRollitt     1  If only f i had come in on my usual day! Such ...
3      BenBarbossa     1  Maybe, maybe not...  The lovely wife calls me ...
4    BethLynch2020     1  same Oh for sure, it's definitely much better ...
..             ...   ...                                                ...
107  sweetderacine     1  i remember being super scared to talk to you b...
108  twilightfairy     0  Great news! Congrats! I remember this discussi...
109      upsetvet1     1  Jail time  0 0 He owns 3 houses, he needs to p...
110      vkhillier     1  lost ur lil ass that u had, playin wit ya nose...
111          xtina     0  Haha omg how sweet is she! Cute!!! Yes!! #Figh...

[112 rows x 3 columns]

In [189]:
# Remove Emails
df1.Tweets = [re.sub('\S*@\S*\s?', '', sent) for sent in df1.Tweets]
# Remove new line characters
df1.Tweets = [re.sub('\s+', ' ', sent) for sent in df1.Tweets]
# Remove distracting single quotes
df1.Tweets = [re.sub("\'", "", sent) for sent in df1.Tweets]
pprint(df1.Tweets[:1])

0    Sucks ass!!! Back at you sweet lady! You too! ...
Name: Tweets, dtype: object


In [0]:
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))

In [194]:
df1

Username  Ptsd                                             Tweets
0           AFR365     1  [sucks, ass, back, at, you, sweet, lady, you, ...
1     AlishaaHasan     0  [omggggg, agreee, like, first, of, all, what, ...
2       AmyRollitt     1  [if, only, had, come, in, on, my, usual, day, ...
3      BenBarbossa     1  [maybe, maybe, not, the, lovely, wife, calls, ...
4    BethLynch2020     1  [same, oh, for, sure, its, definitely, much, b...
..             ...   ...                                                ...
107  sweetderacine     1  [remember, being, super, scared, to, talk, to,...
108  twilightfairy     0  [great, news, congrats, remember, this, discus...
109      upsetvet1     1  [jail, time, he, owns, houses, he, needs, to, ...
110      vkhillier     1  [lost, ur, lil, ass, that, had, playin, wit, y...
111          xtina     0  [haha, omg, how, sweet, is, she, cute, yes, fi...

[112 rows x 3 columns]

In [192]:
df1.Tweets = list(sent_to_words(df1.Tweets))
print(df1.Tweets[:1])

0    [sucks, ass, back, at, you, sweet, lady, you, ...
Name: Tweets, dtype: object


In [195]:
len(df1.Tweets[0])

15887

In [0]:
# Define functions for stopwords, bigrams, trigrams and lemmatization
def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) if word not in stop_words] for doc in texts]

In [0]:
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [199]:
len(df1.Tweets[13])

4948

In [0]:
# Remove Stop Words
df1.Tweets = remove_stopwords(df1.Tweets)

In [201]:
len(df1.Tweets[13])

2623

In [0]:
# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# python3 -m spacy download en
nlp = spacy.load('en', disable=['parser', 'ner'])

In [0]:
# Do lemmatization keeping only noun, adj, vb, adv
df1.Tweets = lemmatization(df1.Tweets, allowed_postags=['NOUN','ADJ','VERB','ADV'])

In [206]:
len(df1['Tweets'])

112

In [0]:
df1.Tweets = remove_stopwords(df1.Tweets)

In [213]:
len(df1.Tweets)

112

In [0]:
df1.to_csv('Final_lammetized.csv')

**Train test split**

In [0]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(df1[["Username","Tweets"]],df1["Ptsd"] , test_size=0.3, random_state=1)

In [242]:
X_train.shape

(78, 2)

In [243]:
X_test.shape

(34, 2)

**TF-IDF Calculation**

In [0]:
train_tweets = []
test_tweets = []
def listToString(s):
    str1 = " "    
    return (str1.join(s))    

In [251]:
#Creating strlist for Training data
for strlist in X_train.Tweets:
    strg = listToString(strlist)
    train_tweets.append(strg)
print(train_tweets[0:50])

['gotten twice hear live hollow beautiful way change anytime soon thank send lot love dude anytime talk soccer way always remember ask home tomorrow surprise wonderful man birthday shoutout shirt love bedtime jennifermerr status must miss season pretty sure stop season binge watch personal tyra fav sterle torre send well wish lot love thank sometimes good sometimes leave gym early sound man work trigger panic attack huge favorite mine honestly subreddit existential lose confine life also whatsthisbug whatsthisplant good shit future bird identification need subreddit love call whatsthisbird massive trigger warning rape good article read long time hope read find shit love woman man fuck trash fly license finish girl swear baby torre cutest little earth brisket leave right leave perfect anniversary imagine miss else onward upward throw man earth away management experience keep lovely world well place far upfront honest couple month hard come clear ish head energy change share honesty stru

In [252]:
#Creating strlist for Test Data
for strlist in X_test.Tweets:
    strg = listToString(strlist)
    test_tweets.append(strg)
print(test_tweets[0:50])

['izzy wear ked else urge unnecessarily redecorate quarantine trailer wait countdown come thank like bar low start call walk stair commute min think daughter look exactly understand chicken kill want exactly thank awesome work open fridge time brisket spinach chocolate ice content look thank nice come though love glass advance surprised good lean phone use timer squad person person fix serenade opening theme want care aaaa hit daily writing shower quota nap quota talented director talk work neverhaveiever lucky soon love thank love want give spin lead show setting check miniserie proud thank think extra dreamy walking houslow best wait wish work home dad dress friend facetime gorgeous say help kid build impatient completely take dumb use helpful work force tomorrow thank rid apple remote stupid remote low sensitivity stupidly remote move useless universal remote apple work thank friend try work money heist window watch tv phone watch money heist come dub automatically try fix setting w

In [0]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [0]:
vec = TfidfVectorizer(max_features=30000)

In [0]:
#tfidf_df = pd.DataFrame(data=vec.fit_transform(tweetsList).todense(), columns=vec.get_feature_names())

In [0]:
#tfidf_df

In [0]:
train_data = vec.fit_transform(train_tweets)
test_data = vec.fit_transform(test_tweets)

In [257]:
type(train_data)

scipy.sparse.csr.csr_matrix

In [258]:
train_data.shape

(78, 30000)

In [259]:
test_data.shape

(34, 20836)

**LOGISTIC REGRESSION MODEL**

In [0]:
from sklearn.linear_model.logistic import LogisticRegression
logReg = LogisticRegression()

In [263]:
logReg.fit(train_data,y_train)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=None, solver='lbfgs', tol=0.0001, verbose=0,
                   warm_start=False)

In [0]:
from sklearn.model_selection import train_test_split, cross_val_score

In [0]:
scores = cross_val_score(logReg, test_data, y_test, cv=5)

In [268]:
scores

array([0.71428571, 0.71428571, 0.71428571, 0.71428571, 0.66666667])

In [0]:
acc = scores.mean()

In [272]:
acc

0.7047619047619047

In [283]:
print("Accuracy is", acc*100, "percent")

Accuracy is 70.47619047619047 percent
